In [1]:
import numpy as np # linear algebra
import os # accessing directory structure
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import string
import json
import string
import itertools as it
from collections import Counter

import pkg_resources
from symspellpy import SymSpell, Verbosity

In [2]:
for dirname, _, filenames in os.walk('.'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

.\Data exploration.ipynb
.\frequency_dictionary_en_82_765.txt
.\stats.json
.\[136542963336478720] [part 10].txt
.\[136542963336478720] [part 11].txt
.\[136542963336478720] [part 1].txt
.\[136542963336478720] [part 2].txt
.\[136542963336478720] [part 3].txt
.\[136542963336478720] [part 4].txt
.\[136542963336478720] [part 5].txt
.\[136542963336478720] [part 6].txt
.\[136542963336478720] [part 7].txt
.\[136542963336478720] [part 8].txt
.\[136542963336478720] [part 9].txt
.\[142445486236762113] [part 2].txt
.\[142445486236762113] [part 3].txt
.\[142445486236762113].txt
.\[196108688199647232] [part 1].txt
.\[196108688199647232] [part 2].txt
.\[290992075934269442] [part 2].txt
.\[290992075934269442] [part 3].txt
.\[290992075934269442] [part 4].txt
.\[290992075934269442] [part 5].txt
.\[290992075934269442] [part 6].txt
.\[290992075934269442] [part 7].txt
.\[290992075934269442] [part 8].txt
.\[290992075934269442].txt
.\[319897695122882560] [part 2].txt
.\[319897695122882560] [part 3].txt
.\[31

In [3]:
data = json.load(open('.\stats.json'))

stats = pd.DataFrame(data["individual"])
stats

channel  conversations  messages  removed_messages
0    [798755145215246387]            301     13518              4109
1    [722981767828734005]           2038    206878             34615
2    [509616727689134080]           1270     22083              4249
3    [716028613539135494]            290      3086               194
4    [136542963336478720]            239    171542              9172
..                    ...            ...       ...               ...
207  [401524750922416132]            550    215742             18019
208  [196108688199647232]           4115     92380              6847
209  [722979690519724082]            261    261763             29914
210  [401524750922416132]            291    220305             17232
211  [290992075934269442]            169    137637             25400

[212 rows x 4 columns]

In [4]:
def read_file(file):
    '''
    read text file into a list
    '''
    x = open(file,'r', encoding = 'utf-8') 
    y = x.read().replace('\\n', '\n').replace('\t', '\n')    #my dumb way to split lines, replace this for better method
    content = y.splitlines() 
    return content

In [5]:
def Sort_by_user(chat):
    '''
    Sort the chatlog by user
    
    '''
    Sort_by_User = {}
    for i in range(len(chat)):
        if ':' in chat[i] and chat[i][0] != ':':     #check if switch user
            name = chat[i].split(':', 1)[0]
            if name not in Sort_by_User:             #check if it's new user
                Sort_by_User[name] = [chat[i].split(':', 1)[1]]
            else:
                Sort_by_User.update(name = [Sort_by_User[name].append(chat[i].split(':', 1)[1].lstrip())])  #add line under user key
        else:
            Sort_by_User.update(name = [Sort_by_User[name].append(chat[i])])   #if current user continue next line
            
    del Sort_by_User['name']
    return Sort_by_User

In [6]:
chat1 = read_file('.\[136542963336478720] [part 1].txt')

sorted_chat1 = Sort_by_user(chat1)

In [7]:
sorted_chat1

{'Petal': [' I made this',
  'how do i give you permissions',
  'anyways, exploring this as a fill in for tinychat',
  'ha! gave em',
  'makes sense',
  'oh hai',
  'a red one',
  'i get its qik',
  'bet',
  'or tak',
  '!',
  'a dvs',
  'I was mostly curious',
  'lemme set you up with permissions tak',
  'just an option',
  'or we can link it somewhere',
  'im new to this whole thing',
  'Ah interesting',
  'all permissions are set for you',
  'ok i got ti',
  'still havent talked on it',
  'ive seen it being used so i decided to check it out',
  'in the browser atm',
  'k in the broswer version now',
  'how do i make a non expiring one to this voice room',
  'ok awesome',
  'i posted it in casualmods',
  'Sunday might be a good day',
  'i can hear youu',
  'imma link it in the irc',
  'i think theyre cute',
  'just wish people would use them',
  ':smiley: hi',
  'you guys want mod permissions?',
  'a voice chat server guib',
  '@Delta :smiley:',
  'Do you want moderator permissions?'

https://github.com/wolfgarbe/SymSpell

More information here

In [8]:
#create a sym_spell object
sym_spell = SymSpell(max_dictionary_edit_distance=2, prefix_length=7)
dictionary_path = pkg_resources.resource_filename(
    "symspellpy", "frequency_dictionary_en_82_765.txt")
sym_spell.load_dictionary(dictionary_path, 0, 1)



True

In [9]:
def add_dictionary_entries(symspell_obj, words_array):
    '''
    create new entries into symspell frequency dictionary
    '''
    for i in words_array:
        symspell_obj.create_dictionary_entry(i, 1) #I just put 1 frequency, I don't think it matters much?
    return None

In [10]:
#add the usernames to the dictionary so they won't be spell-checked
add_dictionary_entries(sym_spell, sorted_chat1.keys())

In [11]:
def string_correction(phrase):
    '''
    run sym_spell checker through a phrase
    '''
    
    suggestions = sym_spell.lookup_compound(phrase, max_edit_distance=2,
                                        transfer_casing=True)
    return suggestions[0].term          #return the first suggestion



#takes about 10-15minutes to correct spelling for 1 text file(10MB)
def correct_spelling(user_dictionary):
    '''
    Correct the entire user-chat dictionary using string_correction
    '''
    out_d = {}
    for key, val in user_dictionary.items():
        out_val = list(map(string_correction, val))
        out_d[key] = out_val
    
    return out_d

def remove_punctuation(phrase):
    '''
    remove punctutation in a phrase
    '''
    translator = str.maketrans('', '', string.punctuation)
    s = phrase.translate(translator)
    return s

In [13]:
corrected_chat = correct_spelling(sorted_chat1)

In [14]:
corrected_chat

{'Petal': ['I made this',
  'how do i give you permissions',
  'anyways exploring this as a fill in for tiny chat',
  'a gave pm',
  'makes sense',
  'of has',
  'a red one',
  'i get its in',
  'bet',
  'or take',
  '',
  'a dvs',
  'I was mostly curious',
  'lemme set you up with permissions take',
  'just an option',
  'or we can link it somewhere',
  'in new to this whole thing',
  'A interesting',
  'all permissions are set for you',
  'of i got to',
  'still haven talked on it',
  'live seen it being used so i decided to check it out',
  'in the browser atm',
  'a in the browser version now',
  'how do i make a non expiring one to this voice room',
  'of awesome',
  'i posted it in casual mods',
  'Sunday might be a good day',
  'i can hear you',
  'emma link it in the inc',
  'i think there cute',
  'just wish people would use them',
  'smiley i',
  'you guys want mod permissions',
  'a voice chat server glib',
  'Delta smiley',
  'Do you want moderator permissions',
  'stuck ou